# PART 2: EXPLORATORY DATA ANALYSIS

**Objective:** This notebook will explore the generated datasets to draw insights from the patient visits and any relationships between date/times to inform our scheduling & streaming models.

---

In [1]:
# Data Management & Manipulation
import numpy as np
import pandas as pd

# Data Visualization
import geopandas as gpd
import folium
import folium.plugins as plugins
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
import seaborn as sns
# from pandas_profiling import ProfileReport, profile_report
from plotly.subplots import make_subplots
# from plotnine import ggplot, aes, geom_jitter, scale_color_manual, theme, labs, theme_bw

# Utils
import datetime
import ipywidgets as widgets
import random
import warnings
from IPython.display import display, HTML
from ipywidgets import interact, interact_manual
from time import sleep
%matplotlib inline
sns.set_style('white')
sns.set_color_codes()
plt.style.use('default')  # sub 'dark_background'
warnings.filterwarnings("ignore")

---
---

## 2A: Setup

**Objective**: Read in patients and clinic data for exploratory analysis.

---

In [2]:
patients_df = pd.read_csv('./uc_past_patients.csv', index_col='pt_id')
patients_df

pt_name      pt_dob  pt_age visit_location    visit_reason  \
pt_id                                                                           
1000055     Rachel Sanchez  1979-09-25      42         denver  cold/flu/fever   
1000025     Patricia Blair  1986-01-18      36         denver  blood/lab-work   
1000032       Juan Holland  2022-04-25       0         denver  cold/flu/fever   
1000028     Kristine Smith  1997-10-31      24         denver        diarrhea   
1000045       Jessica Hale  1967-10-04      54         denver     sore-throat   
...                    ...         ...     ...            ...             ...   
5019174     Nancy Hamilton  1961-06-09      60       lakewood       drug-test   
5019159    William Spencer  1969-02-05      53       lakewood        headache   
5019154     Andrew Daniels  1989-06-28      32       lakewood     vaccination   
5019136     Zachary Hughes  2018-06-04       3       lakewood    stomach-pain   
5019157  Stephanie Summers  1967-05-13      54       lakewood  cold/flu/fever   

         visit_code  visit_date visit_day checkin_time checkout_time  \
pt_id                                                                  
1000055           4  2021-05-01  Saturday     14:56:55      15:39:55   
1000025           3  2021-05-01  Saturday     15:07:59      15:40:59   
1000032           4  2021-05-01  Saturday     15:11:26      15:57:26   
1000028           5  2021-05-01  Saturday     15:12:58      16:26:58   
1000045           4  2021-05-01  Saturday     15:15:54      15:37:54   
...             ...         ...       ...          ...           ...   
5019174           3  2022-04-30  Saturday     19:05:33      19:30:33   
5019159           5  2022-04-30  Saturday     19:12:21      19:47:21   
5019154           3  2022-04-30  Saturday     19:26:48      20:00:48   
5019136           5  2022-04-30  Saturday     19:31:58      20:40:58   
5019157           4  2022-04-30  Saturday     19:48:36      20:36:36   

         rolling_ct  
pt_id                
1000055           1  
1000025           2  
1000032           3  
1000028           4  
1000045           5  
...             ...  
5019174           7  
5019159           8  
5019154           5  
5019136           5  
5019157           4  

[77047 rows x 11 columns]

In [3]:
clinics_df = pd.read_csv('./uc_clinics.csv', index_col='branch_name')
clinics_df

lat         lon  to_denver  to_edgewater  to_wheatridge  \
branch_name                                                                  
denver       39.739064 -104.989697        0.0           5.1            6.3   
edgewater    39.753954 -105.067788        5.0           0.0            2.0   
wheatridge   39.766857 -105.081983        6.3           2.0            0.0   
rino         39.767328 -104.981132        1.9           7.8            7.5   
lakewood     39.704552 -105.079883        7.5           4.3           12.0   

             to_rino  to_lakewood  \
branch_name                         
denver           2.0          8.0   
edgewater        7.7          4.4   
wheatridge       7.8          4.8   
rino             0.0         10.7   
lakewood        11.0          0.0   

                                                nearby_clinics  
branch_name                                                     
denver                     [('rino', 2.0), ('edgewater', 5.1)]  
edgewater    [('wheatridge', 2.0), ('lakewood', 4.4), ('den...  
wheatridge             [('edgewater', 2.0), ('lakewood', 4.8)]  
rino                                         [('denver', 1.9)]  
lakewood                                  [('edgewater', 4.3)]

---
---

## 2B: Initial Explorations

**Objective**: Conduct initial explorations on the raw data without further aggregation or feature engineering.

---

#### Examine data characteristics & summary statistics of patient records:

In [4]:
patients_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 77047 entries, 1000055 to 5019157
Data columns (total 11 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   pt_name         77047 non-null  object
 1   pt_dob          77047 non-null  object
 2   pt_age          77047 non-null  int64 
 3   visit_location  77047 non-null  object
 4   visit_reason    77047 non-null  object
 5   visit_code      77047 non-null  int64 
 6   visit_date      77047 non-null  object
 7   visit_day       77047 non-null  object
 8   checkin_time    77047 non-null  object
 9   checkout_time   77047 non-null  object
 10  rolling_ct      77047 non-null  int64 
dtypes: int64(3), object(8)
memory usage: 7.1+ MB


In [5]:
# Get descriptive stats of continuous variables
patients_df[['pt_age', 'rolling_ct']].describe()

pt_age    rolling_ct
count  77047.000000  77047.000000
mean      34.478669      5.928433
std       20.859070      3.762267
min        0.000000      1.000000
25%       18.000000      3.000000
50%       32.000000      5.000000
75%       50.000000      8.000000
max       80.000000     26.000000

#### Visually explore value counts & distributions:

In [6]:
fig = make_subplots(
    rows=1, cols=2, 
    specs=[[{'type':'domain'}, {'type':'xy'}]], 
    column_widths=[0.35, 0.65], 
    subplot_titles=['Patient Distribution by Clinic', 'Location Breakdown by Severity']
)

# Construct pie-chart based on patient count for each clinic location
location_counts = patients_df['visit_location'].value_counts()
pie = go.Pie(values=location_counts, labels=location_counts.index.str.capitalize(), textinfo='label+percent', showlegend=False)

# Construct histogram for patient count by location stratified by severity level
hist1 = go.Histogram(x=patients_df[patients_df.visit_code==3]['visit_location'], name='Level 3', marker_color='khaki')
hist2 = go.Histogram(x=patients_df[patients_df.visit_code==4]['visit_location'], name='Level 4', marker_color='coral')
hist3 = go.Histogram(x=patients_df[patients_df.visit_code==5]['visit_location'], name='Level 5', marker_color='firebrick')

# Add subplots to figure object
fig.add_trace(pie, row=1, col=1)
fig.add_trace(hist3, row=1, col=2)
fig.add_trace(hist2, row=1, col=2)
fig.add_trace(hist1, row=1, col=2)

# Output figure with custom modifications
fig.update_layout(height=600, width=1100, showlegend=True, barmode='stack')
fig.show()

The figure above...

In [7]:
df = patients_df.copy().sort_values(by='visit_code')
fig = px.histogram(df, x='visit_reason', text_auto=True, color='visit_code', color_discrete_sequence=['khaki', 'coral', 'firebrick'])
fig.update_layout(height=600, width=1200, title_text='Patient Count by Reason')
fig.update_xaxes(categoryorder='total ascending')
fig.show()

The figure above...

In [8]:
fig = px.histogram(patients_df, x='pt_age', text_auto=False, color_discrete_sequence=['darkcyan'])
fig.update_layout(height=400, width=1000, title_text='Patient Count by Age')
fig.show()

The figure above...

---
---

## 2C: Aggregated Explorations

**Objective**: Closely examine relationships within the dataset through aggregated groupings & feature engineering.

---

In [9]:
patients_df

pt_name      pt_dob  pt_age visit_location    visit_reason  \
pt_id                                                                           
1000055     Rachel Sanchez  1979-09-25      42         denver  cold/flu/fever   
1000025     Patricia Blair  1986-01-18      36         denver  blood/lab-work   
1000032       Juan Holland  2022-04-25       0         denver  cold/flu/fever   
1000028     Kristine Smith  1997-10-31      24         denver        diarrhea   
1000045       Jessica Hale  1967-10-04      54         denver     sore-throat   
...                    ...         ...     ...            ...             ...   
5019174     Nancy Hamilton  1961-06-09      60       lakewood       drug-test   
5019159    William Spencer  1969-02-05      53       lakewood        headache   
5019154     Andrew Daniels  1989-06-28      32       lakewood     vaccination   
5019136     Zachary Hughes  2018-06-04       3       lakewood    stomach-pain   
5019157  Stephanie Summers  1967-05-13      54       lakewood  cold/flu/fever   

         visit_code  visit_date visit_day checkin_time checkout_time  \
pt_id                                                                  
1000055           4  2021-05-01  Saturday     14:56:55      15:39:55   
1000025           3  2021-05-01  Saturday     15:07:59      15:40:59   
1000032           4  2021-05-01  Saturday     15:11:26      15:57:26   
1000028           5  2021-05-01  Saturday     15:12:58      16:26:58   
1000045           4  2021-05-01  Saturday     15:15:54      15:37:54   
...             ...         ...       ...          ...           ...   
5019174           3  2022-04-30  Saturday     19:05:33      19:30:33   
5019159           5  2022-04-30  Saturday     19:12:21      19:47:21   
5019154           3  2022-04-30  Saturday     19:26:48      20:00:48   
5019136           5  2022-04-30  Saturday     19:31:58      20:40:58   
5019157           4  2022-04-30  Saturday     19:48:36      20:36:36   

         rolling_ct  
pt_id                
1000055           1  
1000025           2  
1000032           3  
1000028           4  
1000045           5  
...             ...  
5019174           7  
5019159           8  
5019154           5  
5019136           5  
5019157           4  

[77047 rows x 11 columns]

#### Explore daily patient count aggregated by the day of the week:

In [10]:
# Track the number of days in past year broken down by the day of the week
uniq_days = patients_df.groupby(['visit_date', 'visit_day']).count().reset_index(drop=False)[['visit_date', 'visit_day']]
uniq_days.visit_day.value_counts()

Saturday     53
Sunday       52
Monday       52
Tuesday      52
Wednesday    52
Thursday     52
Friday       52
Name: visit_day, dtype: int64

In [11]:
# Aggregate patients data based on daily count broken down by location and day of week
num_pts_per_day = patients_df.groupby(['visit_location', 'visit_day']).count()[['rolling_ct']].reset_index(drop=False)
num_pts_per_day['avg_num_pts'] = num_pts_per_day[['rolling_ct', 'visit_day']].apply(lambda x: round(x[0]/53, 1) if x[1] in ['Saturday'] else round(x[0]/52, 1), axis=1)

# Sort value types for plot outputs to be in desired order
num_pts_per_day['order'] = num_pts_per_day.visit_day.map({'Monday': 0, 'Tuesday': 1, 'Wednesday': 2, 'Thursday': 3, 'Friday': 4, 'Saturday': 5, 'Sunday': 6})
num_pts_per_day = num_pts_per_day.sort_values(by='order')

# Plot average number of patients broken down by day of week, stratified by location
fig = px.bar(
    num_pts_per_day, x='visit_day', y='avg_num_pts', 
    color='visit_location', barmode='group', 
    text='avg_num_pts', title='Average Number of Patients per Day & Clinic',
    labels={'visit_day': 'Day of the Week', 'avg_num_pts': 'Avg. Number of Patients'}
)
fig.update_traces(textposition='outside', cliponaxis=False, textfont_size=10)
fig.show()

The figure above shows...

#### Explore differences between weekday vs. weekend:

In [12]:
# Create attribute of boolean representing if visit_day falls on Saturday/Sunday
patients_df['weekend'] = patients_df.visit_day.map(lambda x: 1 if x in ['Saturday', 'Sunday'] else 0)

# Aggregate patients day based on visit_day falling on weekday or weekend
weekend_df = patients_df.groupby(['visit_location', 'weekend']).count()[['rolling_ct']].reset_index(drop=False)
weekend_df['avg_num_pts'] = weekend_df[['rolling_ct', 'weekend']] \
    .apply(lambda x: round(x[0]/105, 1) if x[1] == 1 else round(x[0]/260, 1), axis=1)

# Plot average number of patients on weekdays and weekends, broken down by location
fig = px.bar(
    weekend_df, x='weekend', y='avg_num_pts', 
    color='visit_location', barmode='group', 
    text='avg_num_pts', title='Average Number of Patients Per Clinic (Weekdays vs Weekend)',
    labels={'weekend': 'Day Type', 'avg_num_pts': 'Avg. Number of Patients'}
)
for idx in range(len(fig.data)):
    fig.data[idx].x = ['Weekday', 'Weekend']
fig.update_traces(textposition='outside', cliponaxis=False, textfont_size=10)
fig.show()

The figure above shows...

---
---

## 2_: Daily Influx Explorations

**Objective**: Visually explore patient influx rate to inform scheduler process.

---

In [15]:
# Create iterable objects that are desired for toggle menus
locations = patients_df.visit_location.unique().tolist()
dates = patients_df.visit_date.unique().tolist()

@interact
def generate_daily_dist(date=dates, first_location=locations, second_location=locations):
    """Produces rolling-count distributions that can be toggled through for specific locations & dates."""
    
    # Convert specific times to grouped versions
    df = patients_df.copy()
    df['checkin_time'] = df.checkin_time.apply(lambda x: x[:-3])
    
    # Create subset data for desired date and the two locations to compare
    df1 = df[(df.visit_date == date) & (df.visit_location == first_location)]
    df2 = df[(df.visit_date == date) & (df.visit_location == second_location)]

    # Construct plot for each subset 
    fig = go.FigureWidget()
    
    # Construct barplot for patient count by location stratified by severity level
    fig = go.Figure()
    bar1 = go.Bar(
        x=df1['checkin_time'], y=df1['rolling_ct'], 
        name=f'Pt. Count @ {first_location.capitalize()} clinic', marker_color='red'
    )
    bar2 = go.Bar(
        x=df2['checkin_time'], y=df2['rolling_ct'], 
        name=f'Pt. Count @ {second_location.capitalize()} clinic', marker_color='blue'
    )

    # Add subplots to figure object
    fig.add_trace(bar1)
    fig.add_trace(bar2)

    # Output figure with custom modifications
    order = sorted(df1.checkin_time.tolist() + df2.checkin_time.tolist())
    fig.update_xaxes(categoryorder='array', categoryarray=order)
    fig.update_traces(opacity=0.3)
    fig.update_layout(height=500, width=1200, showlegend=True, barmode='overlay')
    fig.show()

interactive(children=(Dropdown(description='date', options=('2021-05-01', '2021-05-02', '2021-05-03', '2021-05…

The interactive widget above lets us explore the rolling patient count of two clinics for any date to examine the influx patterns....

---
---

## 2_: Geographic Explorations

**Objective**: Explore dataset attributes within a geospatial context.

---

#### Construct Folium map that indicates a clinic's patient influx for a particular date & time:

In [14]:
# Create iterable objects that are desired for toggle menus
dates = patients_df.visit_date.unique().tolist()
times = { '08': '8am', '09': '9am', '10': '10am', '11': '11am', '12': '12pm', '13': '1pm', 
          '14': '2pm', '15': '3pm', '16': '4pm', '17': '5pm', '18': '6pm', '19': '7pm', '20': '8pm'}

@interact
def map_daily_influx(date=dates, time=list(times.values())):
    """Produces Folium map of each clinic with indicated influx level based on date & time of interest."""
    
    df = patients_df.copy()
    
    # Bin check-in times by hour and get max rolling_ct of hour for simpler visual
    df['checkin_time'] = df.checkin_time.apply(lambda x: x[:2])
    df['checkin_time'] = df.checkin_time.map(times)
    df = df.groupby(['visit_location', 'visit_date', 'checkin_time']).max()[['rolling_ct']].reset_index(drop=False)
    
    # Gather clinic coordinates for map
    df['lat'] = df.visit_location.map(clinics_df.to_dict()['lat'])
    df['lon'] = df.visit_location.map(clinics_df.to_dict()['lon'])
    
    # Filter dataframe based on desired input date and time
    df = df[(df.visit_date == date) & (df.checkin_time == time)]
    
    # Duplicate records based on rolling count of patients for cluster-map
    df = df.loc[df.index.repeat(df['rolling_ct'])]

    # Instantiate Folium map based on Denver, CO's base coordinates
    m = folium.Map(location=[39.74, -105], zoom_start=13, min_zoom=10, max_zoom=14)
    marker = plugins.MarkerCluster(name='Patient Count').add_to(m)
    
    # Add a marker for every record in the filtered data, use a clustered view
    for row in df.iterrows():
        folium.Marker(location=[row[1]['lat'], row[1]['lon']]).add_to(marker)
    
    folium.LayerControl().add_to(m)

    display(m)

interactive(children=(Dropdown(description='date', options=('2021-05-01', '2021-05-02', '2021-05-03', '2021-05…

The interactive widget above lets us visualize the geographic locations of each clinic & explore the rolling patient count at any desired time....

---
---

## 2_: 

**Objective**: 

---